# MVP - Engenharia de Dados
## Autor: Marcel Antonio Lopes Pereira

## Objetivo:

Este MVP tem como objetivo construir um pipeline de dados utilizando tecnologias em nuvem para buscar, coletar, modelar, carregar e analisar dados históricos do futebol de seleções masculinas. O propósito central é responder a uma questão amplamente debatida entre torcedores e especialistas:

**Existe alguma seleção nacional masculina dominante na história do futebol a ponto de ser considerada a melhor de todos os tempos?**

Para explorar essa questão, o pipeline permitirá a análise de algumas perguntas-chave, que ajudarão a identificar as seleções que se destacaram ao longo da história:

1. **Qual seleção tem o maior número de vitórias em jogos oficiais e amistosos?**  
   Identificar as seleções com o maior número de vitórias em diferentes tipos de jogos, fornecendo uma base para medir a consistência no desempenho.

2. **Qual seleção tem a melhor taxa de aproveitamento (pontos ganhos por jogo)?**  
   Avaliar a eficiência das seleções, levando em consideração o número de pontos conquistados em relação aos jogos disputados, ajudando a medir o desempenho em termos de consistência.

3. **Qual seleção tem o maior saldo de gols (gols marcados - gols sofridos) em toda a história?**  
   Analisar o saldo de gols das seleções, refletindo sua capacidade ofensiva e defensiva ao longo do tempo.

4. **Qual seleção tem o maior número de vitórias contra outras grandes seleções (top 10 do ranking da FIFA)?**  
   Analisar o desempenho das seleções contra as mais fortes equipes do mundo, refletindo sua competitividade no cenário global.

5. **Qual seleção tem a maior sequência invicta em toda a história?**  
   Identificar quais seleções mantiveram longas sequências sem derrotas, um bom indicativo de consistência e resistência ao longo do tempo.

6. **Qual seleção tem o maior número de jogos sem sofrer gols em toda a história?**  
   Analisar a capacidade defensiva das seleções, refletindo uma defesa sólida e organização tática eficaz ao longo dos anos.

7. **Quais seleções tiveram os artilheiros mais consistentes e como o desempenho desses jogadores está relacionado com o sucesso da equipe?**  
   Relacionar o desempenho individual dos artilheiros com o desempenho da seleção, ajudando a identificar como a contribuição dos goleadores impactou as vitórias e o sucesso da equipe ao longo da história.



## Estrutura do Pipeline

O pipeline de dados será estruturado em três camadas principais:

- **Bronze:** coleta e armazenamento dos dados brutos conforme os arquivos originais.  
- **Silver:** limpeza, padronização e transformação dos dados brutos, garantindo consistência e qualidade para as análises. Nesta etapa, serão tratados problemas como dados ausentes, duplicidades e formatação inadequada.  
- **Gold:** modelagem analítica dos dados para responder às perguntas de negócio, além da otimização para consultas complexas, garantindo eficiência na extração de insights e facilitando a análise exploratória e preditiva.

A análise final dos dados será realizada em um notebook específico, onde todas as perguntas levantadas serão respondidas. A partir dos resultados obtidos, será possível avaliar, com base em dados, quais seleções se destacam historicamente e se alguma delas pode ser considerada a mais dominante de todos os tempos.





## Busca dos dados:

Na busca dos dados necessários para solução do problema, foi escolhida o Kaggle como fonte para obtenção dos mesmos. Nesse processo, foram escolhidos dois conjuntos de dados que são descritos a seguir.

O primeiro conjunto é referente aos resultados de partidas entre seleções no período entre 1872 e 2025. Nesses dados não estão incluídos os resultados de partidas em Jogos Olímípicos, com seleções nacionais B, sub-23 e seleções com melhores jogadores de ligas. O link de acesso a esse conjunto de dados é o seguinte:
https://www.kaggle.com/datasets/martj42/international-football-results-from-1872-to-2017

Esses dados foram publicados pelo usuário Mart Jürisoo e são de domínio público (CC0: Public Domain). O conjunto possui 4 arquivos do tipo csv: results.csv (resultados das partidas); shootouts.csv (disputas de penalties); goalscorers.csv (marcadores de gols); former_names.csv (nomes anteriores das equipes).

O segundo conjunto é referente ao Ranking da FIFA de seleções no período de 1992 a 2024. Estão listadas as posições dos times e suas mudanças ao longo do tempo dentro desse intervalo. O link de acesso a esse conjunto de dados é o seguinte:
https://www.kaggle.com/datasets/cashncarry/fifaworldranking

Esses dados forma publicados pelo usuário Alex e também são de domínio público (CC0: Public Domain). Apesar do conjunto possuir 3 arquivos do tipo csv, somente foi utilizado um deles nesse trabalho: fifa_ranking-2024-06-20.csv (Lista de Rankings até 20-06-24).

## Coleta, modelagem e carga dos dados:

Após identificar os dados necessários para o problema, é realizada a coleta e a carga dos mesmos para o ambiente de nuvem. Foi utilizado nesse processo o sistema de armazenamento do Datrabricks com utilização do framework Spark para carga dos dados.


In [0]:
# Importando as bibliotecas necessárias para carga e manipulação das tabelas
import pandas as pd

### Camada Bronze

Na camada bronze, são importados os dados no seu formato bruto a partir dos arquivos csv de origem. São realizados scripts relativos a criação da database onde serão armazenados as tabelas da camada bronze.

In [0]:
%sql
-- Desfazendo o database bronze para ser "recriado"
DROP DATABASE IF EXISTS bronze CASCADE;

In [0]:
%sql 
-- Criando o database bronze
CREATE DATABASE bronze;

Após a criação do database, os arquivos CSV são carregados utilizando a biblioteca Pandas para gerar DataFrames a partir dos respectivos arquivos. Foi realizado download dos arquivos no Kaggle e os mesmos foram salvos no mesmo repositório onde esse Notebook está alocado. Em seguida, esses DataFrames são convertidos para o formato Spark e armazenados como tabelas no sistema de armazenamento em nuvem do Databricks, dentro da camada Bronze do database criado.

In [0]:
# Dicionário com os nomes das tabelas e URLs dos arquivos
csv_files = {
    "results": "https://raw.githubusercontent.com/MarcelLopes7/Engenharia-de-Dados/refs/heads/main/results.csv",
    "shootouts": "https://raw.githubusercontent.com/MarcelLopes7/Engenharia-de-Dados/refs/heads/main/shootouts.csv",
    "goalscorers": "https://raw.githubusercontent.com/MarcelLopes7/Engenharia-de-Dados/refs/heads/main/goalscorers.csv",
    "former_names": "https://raw.githubusercontent.com/MarcelLopes7/Engenharia-de-Dados/refs/heads/main/former_names.csv",
    "fifa_ranking": "https://raw.githubusercontent.com/MarcelLopes7/Engenharia-de-Dados/refs/heads/main/fifa_ranking-2024-06-20.csv"
}

# Loop para carregar, converter e salvar cada arquivo
for table_name, url in csv_files.items():
    # Carregar o CSV como DataFrame Pandas
    df = pd.read_csv(url)
    
    # Converter para DataFrame Spark
    spark_df = spark.createDataFrame(df)
    
    # Salvar como tabela na camada bronze
    spark_df.write.mode("overwrite").saveAsTable(f"bronze.{table_name}")

    print(f"Tabela bronze.{table_name} carregada com sucesso.")


Tabela bronze.results carregada com sucesso.
Tabela bronze.shootouts carregada com sucesso.
Tabela bronze.goalscorers carregada com sucesso.
Tabela bronze.former_names carregada com sucesso.
Tabela bronze.fifa_ranking carregada com sucesso.


Após a execução dos script acima, a camada bronze foi construída com as tabelas. Em seguida, são realizadas verificações Spark SQL para confirmar a criação das tabelas. 


In [0]:
# Lista de tabelas que foram criadas
tables = ["results", "shootouts", "goalscorers", "former_names", "fifa_ranking"]

# Exibindo as 10 primeiras linhas de cada tabela
for table in tables:
    print(f"🔍 Exibindo 10 primeiras linhas da tabela bronze.{table}")
    display(spark.sql(f"SELECT * FROM bronze.{table} LIMIT 10"))

# Exibindo o esquema de cada tabela
for table in tables:
    print(f"📊 Esquema da tabela bronze.{table}")
    spark.sql(f"DESCRIBE TABLE bronze.{table}").show()


🔍 Exibindo 10 primeiras linhas da tabela bronze.results


date home_team away_team home_score away_score tournament city country neutral 1872-11-30 Scotland England 0 0 Friendly Glasgow Scotland false 1873-03-08 England Scotland 4 2 Friendly London England false 1874-03-07 Scotland England 2 1 Friendly Glasgow Scotland false 1875-03-06 England Scotland 2 2 Friendly London England false 1876-03-04 Scotland England 3 0 Friendly Glasgow Scotland false 1876-03-25 Scotland Wales 4 0 Friendly Glasgow Scotland false 1877-03-03 England Scotland 1 3 Friendly London England false 1877-03-05 Wales Scotland 0 2 Friendly Wrexham Wales false 1878-03-02 Scotland England 7 2 Friendly Glasgow Scotland false 1878-03-23 Scotland Wales 9 0 Friendly Glasgow Scotland false

🔍 Exibindo 10 primeiras linhas da tabela bronze.shootouts


date home_team away_team winner first_shooter 1967-08-22 India Taiwan Taiwan null 1971-11-14 South Korea Vietnam Republic South Korea null 1972-05-07 South Korea Iraq Iraq null 1972-05-17 Thailand South Korea South Korea null 1972-05-19 Thailand Cambodia Thailand null 1973-04-21 Senegal Ghana Ghana null 1973-06-14 Guinea Mali Guinea null 1973-06-14 Mauritius Tanzania Mauritius null 1973-07-26 Malaysia Kuwait Malaysia null 1973-07-26 Cambodia Singapore Singapore null

🔍 Exibindo 10 primeiras linhas da tabela bronze.goalscorers


...

🔍 Exibindo 10 primeiras linhas da tabela bronze.former_names


current former start_date end_date Benin Dahomey 1959-11-08 1975-11-30 Burkina Faso Upper Volta 1960-04-14 1984-08-04 Curaçao Netherlands Antilles 1957-03-03 2010-10-10 Czechoslovakia Bohemia 1903-04-05 1919-01-01 Czechoslovakia Bohemia and Moravia 1939-01-01 1945-05-01 Czechoslovakia Representation of Czechs and Slovaks 1993-03-24 1993-11-17 DR Congo Belgian Congo 1948-05-25 1956-01-02 DR Congo Congo-Léopoldville 1963-04-12 1964-07-19 DR Congo Congo-Kinshasa 1965-01-09 1970-11-24 DR Congo Zaïre 1971-01-10 1997-04-27

🔍 Exibindo 10 primeiras linhas da tabela bronze.fifa_ranking


rank country_full country_abrv total_points previous_points rank_change confederation rank_date 140.0 Brunei Darussalam BRU 2.0 0.0 140 AFC 1992-12-31 33.0 Portugal POR 38.0 0.0 33 UEFA 1992-12-31 32.0 Zambia ZAM 38.0 0.0 32 CAF 1992-12-31 31.0 Greece GRE 38.0 0.0 31 UEFA 1992-12-31 30.0 Algeria ALG 39.0 0.0 30 CAF 1992-12-31 29.0 Yugoslavia YUG 39.0 0.0 29 UEFA 1992-12-31 28.0 Wales WAL 40.0 0.0 28 UEFA 1992-12-31 27.0 Côte d'Ivoire CIV 41.0 0.0 27 CAF 1992-12-31 34.0 Austria AUT 38.0 0.0 34 UEFA 1992-12-31 26.0 Bulgaria BUL 41.0 0.0 26 UEFA 1992-12-31

📊 Esquema da tabela bronze.results
+----------+---------+-------+
|  col_name|data_type|comment|
+----------+---------+-------+
|      date|   string|   null|
| home_team|   string|   null|
| away_team|   string|   null|
|home_score|   bigint|   null|
|away_score|   bigint|   null|
|tournament|   string|   null|
|      city|   string|   null|
|   country|   string|   null|
|   neutral|  boolean|   null|
+----------+---------+-------+

📊 Esquema da tabela bronze.shootouts
+-------------+---------+-------+
|     col_name|data_type|comment|
+-------------+---------+-------+
|         date|   string|   null|
|    home_team|   string|   null|
|    away_team|   string|   null|
|       winner|   string|   null|
|first_shooter|   string|   null|
+-------------+---------+-------+

📊 Esquema da tabela bronze.goalscorers
+---------+---------+-------+
| col_name|data_type|comment|
+---------+---------+-------+
|     date|   string|   null|
|home_team|   string|   null|
|away_team|   string|   null

Nesta etapa do projeto, foi concluída a ingestão dos dados brutos provenientes de diversos arquivos CSV históricos relacionados às seleções nacionais de futebol, utilizando o Spark no Databricks. Com a criação de tabelas na camada bronze, os dados foram armazenados em sua forma original, preservando todas as informações com a maior fidelidade possível.

Agora que a camada bronze está criada e os dados estão prontos para análise, a próxima etapa do trabalho será a construção da camada silver, onde será feita a limpeza, transformação e integração dos dados para garantir que estejam no formato adequado para análises mais complexas.

A camada silver será responsável por aprimorar a qualidade dos dados, identificando e corrigindo inconsistências, transformando variáveis e aplicando quaisquer outras transformações necessárias para garantir que os dados estejam prontos para a análise e construção de modelos na camada gold.

Com isso, segue-se para a próxima fase do pipeline de dados, garantindo que os dados estejam cada vez mais preparados para responder às questões relacionadas à dominância das seleções nacionais no futebol.

##  Camada Silver

Neste notebook, será continuado o processo de transformação dos dados, avançando para a construção da camada silver do nosso pipeline de dados. A camada silver tem como objetivo realizar um processamento mais refinado dos dados provenientes da camada bronze, aplicando transformações e limpezas essenciais para garantir que os dados estejam padronizados e prontos para análises mais complexas na camada gold.

Utilizando as tabelas da camada bronze como base, foram realizadas operações como o tratamento de nomes de seleções através da tabela former_names, além de aplicar ajustes nos formatos de dados (como conversões de tipos de variáveis) e, quando necessário, a remoção de dados nulos. As tabelas resultantes da camada silver servirão como um ponto de partida para análises mais profundas e criação de métricas na camada gold.

A seguir, serão processados os principais dados de resultados de partidas, disputas de pênaltis, marcadores de gols e o ranking FIFA para garantir que todas as informações estejam corretamente estruturadas e padronizadas. Ao final deste notebook, haverá tabelas com informações prontas para serem utilizadas em análises avançadas, como a performance das seleções ao longo do tempo.
Primeiramente, são executados scripts de criação do database silver.

In [0]:
%sql DROP DATABASE IF EXISTS silver CASCADE

In [0]:
%sql CREATE DATABASE silver

A partir disso, são criadas as tabelas na camada silver a partir das tabelas da camada Bronze. O processo de criação de cada uma delas é descrito a seguir.

### Tabela Former Names
A primeira tabela a ser criada é a silver.former_names. O código a seguir transforma a tabela bruta bronze.former_names em uma versão refinada (silver.former_names), padronizando formatos de data, verificando sobreposições temporais nos nomes dos times e removendo registros inválidos. Ele converte as datas para o tipo DATE, identifica períodos sobrepostos para o mesmo time (usando a função LAG) e filtra dados inconsistentes (datas invertidas ou nomes nulos). O resultado é uma tabela limpa e validada, pronta para integração com outras bases de dados.

In [0]:
%sql
CREATE OR REPLACE TABLE silver.former_names AS
SELECT 
  current,
  former,
  CAST(start_date AS DATE) AS start_date,
  CAST(end_date AS DATE) AS end_date,
  -- Valida períodos não sobrepostos para o mesmo time
  CASE 
    WHEN LAG(end_date) OVER (PARTITION BY current ORDER BY start_date) >= start_date 
    THEN true 
    ELSE false 
  END AS has_overlap
FROM bronze.former_names
WHERE
  current IS NOT NULL
  AND former IS NOT NULL
  AND start_date <= end_date;

num_affected_rows num_inserted_rows

A seguir, é verificado na tabela se todo o processo foi realizado com sucesso.

In [0]:
%sql
-- Verificação de qualidade dos dados após transformação
WITH checks AS (
  SELECT
    -- Verifica registros processados
    COUNT(*) AS total_records,
    
    -- Verifica conversão de datas
    SUM(CASE WHEN silver.start_date IS NULL OR silver.end_date IS NULL THEN 1 ELSE 0 END) AS null_dates,
    
    -- Verifica sobreposições
    SUM(CASE WHEN silver.has_overlap THEN 1 ELSE 0 END) AS overlapping_periods,
    
    -- Verifica constraints
    SUM(CASE WHEN silver.current IS NULL OR silver.former IS NULL THEN 1 ELSE 0 END) AS null_names,
    SUM(CASE WHEN silver.start_date > silver.end_date THEN 1 ELSE 0 END) AS invalid_date_ranges,
    
    -- Verifica consistência com dados originais
    (SELECT COUNT(*) FROM bronze.former_names) AS source_count,
    (SELECT COUNT(DISTINCT former) FROM bronze.former_names) AS source_unique_names
  FROM silver.former_names silver
)

SELECT
  total_records,
  source_count,
  source_unique_names,
  null_dates,
  overlapping_periods,
  null_names,
  invalid_date_ranges,
  
  -- Relatórios de qualidade
  CASE
    WHEN null_dates = 0 AND null_names = 0 AND invalid_date_ranges = 0 
    THEN '✅ Validações básicas passaram'
    ELSE '❌ Problemas encontrados'
  END AS basic_validation,
  
  CASE
    WHEN total_records <= source_count AND total_records > 0
    THEN '✅ Contagem de registros OK'
    ELSE '❌ Problema na contagem de registros'
  END AS count_validation,
  
  CASE
    WHEN overlapping_periods = 0
    THEN '✅ Nenhuma sobreposição não detectada'
    ELSE CONCAT('⚠️ ', overlapping_periods, ' sobreposições encontradas')
  END AS overlap_validation

FROM checks;

total_records source_count source_unique_names null_dates overlapping_periods null_names invalid_date_ranges basic_validation count_validation overlap_validation 34 34 34 0 0 0 0 ✅ Validações básicas passaram ✅ Contagem de registros OK ✅ Nenhuma sobreposição não detectada

Visualização da tabela criada.

In [0]:
%sql
SELECT *
FROM silver.former_names

current former start_date end_date has_overlap Benin Dahomey 1959-11-08 1975-11-30 false Burkina Faso Upper Volta 1960-04-14 1984-08-04 false Curaçao Netherlands Antilles 1957-03-03 2010-10-10 false Czechoslovakia Bohemia 1903-04-05 1919-01-01 false Czechoslovakia Bohemia and Moravia 1939-01-01 1945-05-01 false Czechoslovakia Representation of Czechs and Slovaks 1993-03-24 1993-11-17 false DR Congo Belgian Congo 1948-05-25 1956-01-02 false DR Congo Congo-Léopoldville 1963-04-12 1964-07-19 false DR Congo Congo-Kinshasa 1965-01-09 1970-11-24 false DR Congo Zaïre 1971-01-10 1997-04-27 false Djibouti French Somaliland 1947-12-05 1977-06-27 false Egypt United Arab Republic 1958-02-22 1971-09-11 false Eswatini Swaziland 1968-05-01 2018-04-19 false Ghana Gold Coast 1950-05-28 1957-03-06 false Guinea-Bissau Portuguese Guinea 1953-06-02 1973-09-24 false Guyana British Guiana 1905-07-21 1967-08-02 false Indonesia Dutch East Indies 1934-05-13 1951-03-04 false Israel Mandatory Palestine 1934-03-16 1940-04-27 false Malawi Nyasaland 1957-08-28 1964-07-04 false Malaysia Malaya 1948-06-20 1963-08-16 false Myanmar Burma 1952-03-14 1989-01-01 false North Macedonia Macedonia 1993-10-13 2018-11-19 false Northern Ireland Ireland 1882-02-18 1956-04-11 false Republic of Ireland Irish Free State 1924-05-28 1936-12-06 false Republic of Ireland Éire 1937-01-01 1953-03-25 false Russia Soviet Union 1924-11-16 1991-11-13 false Russia CIS 1992-01-25 1992-06-18 false Samoa Western Samoa 1979-08-31 1996-11-15 false Sri Lanka Ceylon 1952-03-24 1972-05-22 false Suriname Dutch Guyana 1921-01-28 1975-11-25 false Tanzania Tanganyika 1945-01-01 1964-04-26 false Vanuatu New Hebrides 1951-10-04 1980-07-30 false Zambia Northern Rhodesia 1947-02-22 1964-10-25 false Zimbabwe Southern Rhodesia 1946-06-16 1980-04-18 false

Alterando o nome de um país para evitar conflito de nome com a tabela results.

In [0]:
%sql
UPDATE silver.former_names
SET current = 'Czech Republic'
WHERE current = 'Czechoslovakia';

num_affected_rows 3

In [0]:
%sql
SELECT *
FROM silver.former_names

current former start_date end_date has_overlap Benin Dahomey 1959-11-08 1975-11-30 false Burkina Faso Upper Volta 1960-04-14 1984-08-04 false Curaçao Netherlands Antilles 1957-03-03 2010-10-10 false Czechoslovakia Bohemia 1903-04-05 1919-01-01 false Czechoslovakia Bohemia and Moravia 1939-01-01 1945-05-01 false Czechoslovakia Representation of Czechs and Slovaks 1993-03-24 1993-11-17 false DR Congo Belgian Congo 1948-05-25 1956-01-02 false DR Congo Congo-Léopoldville 1963-04-12 1964-07-19 false DR Congo Congo-Kinshasa 1965-01-09 1970-11-24 false DR Congo Zaïre 1971-01-10 1997-04-27 false Djibouti French Somaliland 1947-12-05 1977-06-27 false Egypt United Arab Republic 1958-02-22 1971-09-11 false Eswatini Swaziland 1968-05-01 2018-04-19 false Ghana Gold Coast 1950-05-28 1957-03-06 false Guinea-Bissau Portuguese Guinea 1953-06-02 1973-09-24 false Guyana British Guiana 1905-07-21 1967-08-02 false Indonesia Dutch East Indies 1934-05-13 1951-03-04 false Israel Mandatory Palestine 1934-03-16 1940-04-27 false Malawi Nyasaland 1957-08-28 1964-07-04 false Malaysia Malaya 1948-06-20 1963-08-16 false Myanmar Burma 1952-03-14 1989-01-01 false North Macedonia Macedonia 1993-10-13 2018-11-19 false Northern Ireland Ireland 1882-02-18 1956-04-11 false Republic of Ireland Irish Free State 1924-05-28 1936-12-06 false Republic of Ireland Éire 1937-01-01 1953-03-25 false Russia Soviet Union 1924-11-16 1991-11-13 false Russia CIS 1992-01-25 1992-06-18 false Samoa Western Samoa 1979-08-31 1996-11-15 false Sri Lanka Ceylon 1952-03-24 1972-05-22 false Suriname Dutch Guyana 1921-01-28 1975-11-25 false Tanzania Tanganyika 1945-01-01 1964-04-26 false Vanuatu New Hebrides 1951-10-04 1980-07-30 false Zambia Northern Rhodesia 1947-02-22 1964-10-25 false Zimbabwe Southern Rhodesia 1946-06-16 1980-04-18 false

Desse modo, essa tabela será agregada com as outras posteriormente de modo que os times estejam registrados com um nome único por todo o período de tempo.

### Tabela Results
A próxima tabela a ser criada é a tabela silver.results. 
O fluxo de construção da tabela silver.results inicia com os dados brutos da camada Bronze (bronze.results) e aplica uma série de transformações essenciais para garantir consistência, qualidade e enriquecimento dos dados.

- Padronização de Datas: Converte date para o tipo DATE para garantir consistência em análises temporais.

- Unificação de Nomes de Times:  Usa silver.former_names para padronizar nomes históricos (ex: "Alemanha Ocidental" → "Alemanha"); Mantém o nome original se não houver correspondência (COALESCE).

- Conversão de Tipos de Dados: Converte home_score e away_score para INT (evitando decimais desnecessários); Transforma neutral em BOOLEAN (TRUE/FALSE).

- Limpeza Básica: Remove registros com placares nulos (WHERE home_score IS NOT NULL); Aplica TRIM() em campos de texto para eliminar espaços extras.

In [0]:
%sql
CREATE OR REPLACE TABLE silver.results AS
SELECT 
  CONCAT(
    CAST(date(r.date) AS STRING), 
    '_', 
    COALESCE(fn_home.current, r.home_team), 
    '_', 
    COALESCE(fn_away.current, r.away_team), 
    '_', 
    CAST(r.home_score AS STRING), 
    '_', 
    CAST(r.away_score AS STRING)
  ) AS match_id,  -- Geração do match_id concatenando as colunas relevantes
  date(r.date) AS match_date,
  COALESCE(fn_home.current, r.home_team) AS home_team,
  COALESCE(fn_away.current, r.away_team) AS away_team,
  CAST(r.home_score AS INT) AS home_score,
  CAST(r.away_score AS INT) AS away_score,
  trim(r.tournament) AS tournament,  -- Apenas remove espaços, sem categorização
  r.city,
  r.country,
  CAST(r.neutral AS BOOLEAN) AS is_neutral
FROM bronze.results r
LEFT JOIN silver.former_names fn_home ON r.home_team = fn_home.former
LEFT JOIN silver.former_names fn_away ON r.away_team = fn_away.former
WHERE r.home_score IS NOT NULL;


num_affected_rows num_inserted_rows

Após as transformações para criação da tabela, é realizada a validação das mesmas.

In [0]:
%sql
-- Verificação de qualidade dos dados após transformação
WITH checks AS (
  SELECT
    -- Verifica registros processados
    COUNT(*) AS total_records,
    
    -- Verifica conversão de tipos e valores nulos
    SUM(CASE WHEN match_id IS NULL THEN 1 ELSE 0 END) AS null_match_ids,
    SUM(CASE WHEN match_date IS NULL THEN 1 ELSE 0 END) AS null_dates,
    SUM(CASE WHEN home_team IS NULL THEN 1 ELSE 0 END) AS null_home_teams,
    SUM(CASE WHEN away_team IS NULL THEN 1 ELSE 0 END) AS null_away_teams,
    SUM(CASE WHEN home_score IS NULL THEN 1 ELSE 0 END) AS null_home_scores,
    SUM(CASE WHEN away_score IS NULL THEN 1 ELSE 0 END) AS null_away_scores,
    
    -- Verifica valores inválidos
    SUM(CASE WHEN home_score < 0 THEN 1 ELSE 0 END) AS negative_home_scores,
    SUM(CASE WHEN away_score < 0 THEN 1 ELSE 0 END) AS negative_away_scores,
    SUM(CASE WHEN home_team = away_team THEN 1 ELSE 0 END) AS same_team_matches,
    
    -- Verifica consistência com dados originais
    (SELECT COUNT(*) FROM bronze.results WHERE home_score IS NOT NULL) AS source_count,
    (SELECT COUNT(DISTINCT home_team) FROM bronze.results) AS source_unique_home_teams
  FROM silver.results
)

SELECT
  total_records,
  source_count,
  source_unique_home_teams,
  
  -- Relatório de nulos
  null_match_ids,
  null_dates,
  null_home_teams,
  null_away_teams,
  null_home_scores,
  null_away_scores,
  
  -- Relatório de valores inválidos
  negative_home_scores,
  negative_away_scores,
  same_team_matches,
  
  -- Resumo de validações
  CASE
    WHEN null_match_ids = 0 AND null_dates = 0 AND null_home_teams = 0 AND 
         null_away_teams = 0 AND null_home_scores = 0 AND null_away_scores = 0 AND
         negative_home_scores = 0 AND negative_away_scores = 0 AND same_team_matches = 0
    THEN '✅ Todas as validações básicas passaram'
    ELSE '❌ Problemas encontrados nos dados'
  END AS basic_validation,
  
  CASE
    WHEN total_records = source_count
    THEN '✅ Contagem de registros OK'
    ELSE CONCAT('❌ Diferença de ', ABS(total_records - source_count), ' registros')
  END AS count_validation,
  
  CASE
    WHEN same_team_matches = 0
    THEN '✅ Nenhum jogo com times iguais'
    ELSE CONCAT('⚠️ ', same_team_matches, ' jogos com times iguais encontrados')
  END AS team_validation,

  CASE
    WHEN negative_home_scores = 0 AND negative_away_scores = 0
    THEN '✅ Todos os placares são válidos'
    ELSE CONCAT('⚠️ ', (negative_home_scores + negative_away_scores), ' placares negativos encontrados')
  END AS score_validation

FROM checks;

total_records source_count source_unique_home_teams null_match_ids null_dates null_home_teams null_away_teams null_home_scores null_away_scores negative_home_scores negative_away_scores same_team_matches basic_validation count_validation team_validation score_validation 48207 48207 324 0 0 0 0 0 0 0 0 0 ✅ Todas as validações básicas passaram ✅ Contagem de registros OK ✅ Nenhum jogo com times iguais ✅ Todos os placares são válidos

São incluídos comentários descrevendo a tabela e seus atributos.

In [0]:
%sql
-- Comentário da tabela
ALTER TABLE silver.results 
SET TBLPROPERTIES (
  'comment' = 'Tabela de resultados de partidas de futebol internacionais. Contém dados brutos padronizados para uso na camada Gold. Fonte: bronze.results.'
);

-- Comentários das colunas (um comando por coluna)
ALTER TABLE silver.results CHANGE COLUMN match_id match_id STRING COMMENT 'Código único de identificação da partida. Domínio: Até 100 caracteres.';
ALTER TABLE silver.results CHANGE COLUMN match_date match_date DATE COMMENT 'Data da partida no formato YYYY-MM-DD. Domínio: Datas entre 1872-11-30 (primeiro jogo internacional) e a data atual.';
ALTER TABLE silver.results CHANGE COLUMN home_team home_team STRING COMMENT 'Nome do time da casa padronizado. Domínio: Valores da tabela silver.teams (ex: "Brazil", "Germany").';
ALTER TABLE silver.results CHANGE COLUMN away_team away_team STRING COMMENT 'Nome do time visitante padronizado. Domínio: Valores da tabela silver.teams.';
ALTER TABLE silver.results CHANGE COLUMN home_score home_score INT COMMENT 'Gols marcados pelo time da casa. Domínio: Inteiro ≥ 0 (valores nulos substituídos por 0).';
ALTER TABLE silver.results CHANGE COLUMN away_score away_score INT COMMENT 'Gols marcados pelo time visitante. Domínio: Inteiro ≥ 0 (valores nulos substituídos por 0).';
ALTER TABLE silver.results CHANGE COLUMN tournament tournament STRING COMMENT 'Nome do torneio sem formatação adicional. Domínio: Texto livre (ex: "FIFA World Cup", "Copa América").';
ALTER TABLE silver.results CHANGE COLUMN city city STRING COMMENT 'Cidade onde a partida foi realizada. Domínio: Texto livre (ex: "Rio de Janeiro", "Berlin").';
ALTER TABLE silver.results CHANGE COLUMN country country STRING COMMENT 'País onde a partida foi realizada. Domínio: Nomes de países ISO 3166 (ex: "Brazil", "Spain").';
ALTER TABLE silver.results CHANGE COLUMN is_neutral is_neutral BOOLEAN COMMENT 'Indica se o jogo foi em local neutro. Domínio: TRUE/FALSE.';

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-1088646733164508>:17
     15     display(df)
     16     return df
---> 17   _sqldf = ____databricks_percent_sql()
     18 finally:
     19   del ____databricks_percent_sql

File <command-1088646733164508>:13, in ____databricks_percent_sql()
     11 spark.sql(base64.standard_b64decode("QUxURVIgVEFCTEUgc2lsdmVyLnJlc3VsdHMgQ0hBTkdFIENPTFVNTiB0b3VybmFtZW50IHRvdXJuYW1lbnQgU1RSSU5HIENPTU1FTlQgJ05vbWUgZG8gdG9ybmVpbyBzZW0gZm9ybWF0YcOnw6NvIGFkaWNpb25hbC4gRG9tw61uaW86IFRleHRvIGxpdnJlIChleDogIkZJRkEgV29ybGQgQ3VwIiwgIkNvcGEgQW3DqXJpY2EiKS4n").decode())
     12 spark.sql(base64.standard_b64decode("QUxURVIgVEFCTEUgc2lsdmVyLnJlc3VsdHMgQ0hBTkdFIENPTFVNTiBjaXR5IGNpdHkgU1RSSU5HIENPTU1FTlQgJ0NpZGFkZSBvbmRlIGEgcGFydGlkYSBmb2kgcmVhbGl6YWRhLiBEb23DrW5pbzogVGV4dG8gbGl2cmUgKGV4OiAiUmlvIGRlIEphbmVpcm8iLCAiQmVybGluIikuJw==").decode())
---> 13 spar

In [0]:
%sql
DESCRIBE TABLE EXTENDED silver.results;

col_name data_type comment match_id string Código único de identificação da partida. Domínio: Até 100 caracteres. match_date date Data da partida no formato YYYY-MM-DD. Domínio: Datas entre 1872-11-30 (primeiro jogo internacional) e a data atual. home_team string Nome do time da casa padronizado. Domínio: Valores da tabela silver.teams (ex: "Brazil", "Germany"). away_team string Nome do time visitante padronizado. Domínio: Valores da tabela silver.teams. home_score int Gols marcados pelo time da casa. Domínio: Inteiro ≥ 0 (valores nulos substituídos por 0). away_score int Gols marcados pelo time visitante. Domínio: Inteiro ≥ 0 (valores nulos substituídos por 0). tournament string Nome do torneio sem formatação adicional. Domínio: Texto livre (ex: "FIFA World Cup", "Copa América"). city string Cidade onde a partida foi realizada. Domínio: Texto livre (ex: "Rio de Janeiro", "Berlin"). country string null is_neutral boolean null # Detailed Table Information Catalog spark_catalog Database silver Table results Created Time Tue Apr 01 23:18:55 UTC 2025 Last Access UNKNOWN Created By Spark 3.3.2 Statistics 3517101 bytes Type MANAGED Comment Tabela de resultados de partidas de futebol internacionais. Contém dados brutos padronizados para uso na camada Gold. Fonte: bronze.results. Location dbfs:/user/hive/warehouse/silver.db/results Provider delta Owner root Is_managed_location true Table Properties [delta.minReaderVersion=1,delta.minWriterVersion=2]

É verificada a criação da tabela.

In [0]:
%sql
-- Verificar a tabela silver.results
SELECT * FROM silver.results LIMIT 20;

match_id match_date home_team away_team home_score away_score tournament city country is_neutral 1872-11-30_Scotland_England_0_0 1872-11-30 Scotland England 0 0 Friendly Glasgow Scotland false 1873-03-08_England_Scotland_4_2 1873-03-08 England Scotland 4 2 Friendly London England false 1874-03-07_Scotland_England_2_1 1874-03-07 Scotland England 2 1 Friendly Glasgow Scotland false 1875-03-06_England_Scotland_2_2 1875-03-06 England Scotland 2 2 Friendly London England false 1876-03-04_Scotland_England_3_0 1876-03-04 Scotland England 3 0 Friendly Glasgow Scotland false 1876-03-25_Scotland_Wales_4_0 1876-03-25 Scotland Wales 4 0 Friendly Glasgow Scotland false 1877-03-03_England_Scotland_1_3 1877-03-03 England Scotland 1 3 Friendly London England false 1877-03-05_Wales_Scotland_0_2 1877-03-05 Wales Scotland 0 2 Friendly Wrexham Wales false 1878-03-02_Scotland_England_7_2 1878-03-02 Scotland England 7 2 Friendly Glasgow Scotland false 1878-03-23_Scotland_Wales_9_0 1878-03-23 Scotland Wales 9 0 Friendly Glasgow Scotland false 1879-01-18_England_Wales_2_1 1879-01-18 England Wales 2 1 Friendly London England false 1879-04-05_England_Scotland_5_4 1879-04-05 England Scotland 5 4 Friendly London England false 1879-04-07_Wales_Scotland_0_3 1879-04-07 Wales Scotland 0 3 Friendly Wrexham Wales false 1880-03-13_Scotland_England_5_4 1880-03-13 Scotland England 5 4 Friendly Glasgow Scotland false 1880-03-15_Wales_England_2_3 1880-03-15 Wales England 2 3 Friendly Wrexham Wales false 1880-03-27_Scotland_Wales_5_1 1880-03-27 Scotland Wales 5 1 Friendly Glasgow Scotland false 1881-02-26_England_Wales_0_1 1881-02-26 England Wales 0 1 Friendly Blackburn England false 1881-03-12_England_Scotland_1_6 1881-03-12 England Scotland 1 6 Friendly London England false 1881-03-14_Wales_Scotland_1_5 1881-03-14 Wales Scotland 1 5 Friendly Wrexham Wales false 1882-02-18_Northern Ireland_England_0_13 1882-02-18 Northern Ireland England 0 13 Friendly Belfast Ireland false

### Tabela Shootouts
O fluxo de construção da tabela shootouts na camada Silver segue uma sequência lógica de transformações a partir dos dados brutos:

- Padronização de Datas: Converte date para DATE.

- Unificação de Nomes de Times: Padroniza home_team, away_team e winner usando bronze.former_names.

- Preservação de Dados Originais: Mantém first_shooter (time que bateu primeiro) sem modificações.

- Filtro de Qualidade: Não remove registros (todos os pênaltis são considerados válidos).

In [0]:
%sql
CREATE OR REPLACE TABLE silver.shootouts AS
SELECT 
  r.match_id,  -- Usando o match_id da tabela results já existente
  date(s.date) AS match_date,
  COALESCE(fn_home.current, s.home_team) AS home_team,
  COALESCE(fn_away.current, s.away_team) AS away_team,
  COALESCE(fn_winner.current, s.winner) AS winner,
  COALESCE(s.first_shooter, 'Unknown') AS first_shooter
FROM bronze.shootouts s
JOIN silver.results r
  ON r.home_team = s.home_team
  AND r.away_team = s.away_team
  AND r.match_date = date(s.date)
LEFT JOIN silver.former_names fn_home ON s.home_team = fn_home.former
LEFT JOIN silver.former_names fn_away ON s.away_team = fn_away.former
LEFT JOIN silver.former_names fn_winner ON s.winner = fn_winner.former;


num_affected_rows num_inserted_rows

São verificadas as transformações.

In [0]:
%sql
WITH checks AS (
  SELECT
    COUNT(*) AS total_records,
    
    -- Verificação de valores nulos
    SUM(CASE WHEN match_id IS NULL THEN 1 ELSE 0 END) AS null_match_ids,
    SUM(CASE WHEN match_date IS NULL THEN 1 ELSE 0 END) AS null_dates,
    SUM(CASE WHEN home_team IS NULL THEN 1 ELSE 0 END) AS null_home_teams,
    SUM(CASE WHEN away_team IS NULL THEN 1 ELSE 0 END) AS null_away_teams,
    SUM(CASE WHEN winner IS NULL THEN 1 ELSE 0 END) AS null_winners,
    
    -- Verificação específica para first_shooter
    SUM(CASE WHEN first_shooter = 'Unknown' THEN 1 ELSE 0 END) AS unknown_shooters,
    
    -- Verificação de consistência
    SUM(CASE WHEN winner NOT IN (home_team, away_team) AND winner IS NOT NULL THEN 1 ELSE 0 END) AS invalid_winners,
    
    -- Verificação de integridade referencial
    (SELECT COUNT(*) FROM bronze.shootouts) AS source_count,
    (SELECT COUNT(*) FROM silver.results) AS reference_results_count,
    COUNT(DISTINCT match_id) AS unique_match_ids
  FROM silver.shootouts
)

SELECT
  total_records,
  source_count,
  reference_results_count,
  unique_match_ids,
  
  -- Relatório de nulos
  null_match_ids,
  null_dates,
  null_home_teams,
  null_away_teams,
  null_winners,
  
  -- Relatório de first_shooter
  unknown_shooters,
  
  -- Relatório de consistência
  invalid_winners,
  
  -- Resumo de validações
  CASE
    WHEN null_match_ids = 0 AND null_dates = 0 AND null_home_teams = 0 AND 
         null_away_teams = 0 AND null_winners = 0
    THEN '✅ Validações básicas passaram'
    ELSE '❌ Problemas encontrados nos dados'
  END AS basic_validation,
  
  CASE
    WHEN total_records <= source_count AND total_records > 0
    THEN '✅ Contagem de registros OK'
    ELSE CONCAT('❌ Diferença de ', ABS(total_records - source_count), ' registros')
  END AS count_validation,
  
  CASE
    WHEN invalid_winners = 0
    THEN '✅ Todos os vencedores são times participantes'
    ELSE CONCAT('⚠️ ', invalid_winners, ' vencedores inválidos encontrados')
  END AS winner_validation,
  
  CASE
    WHEN unknown_shooters = 0
    THEN '✅ Todos os primeiros cobradores estão identificados'
    ELSE CONCAT('ℹ️ ', unknown_shooters, ' primeiros cobradores marcados como "Unknown"')
  END AS shooter_validation,
  
  CASE
    WHEN unique_match_ids = total_records
    THEN '✅ Todos os match_ids são únicos'
    ELSE CONCAT('⚠️ ', (total_records - unique_match_ids), ' match_ids duplicados')
  END AS match_id_validation

FROM checks;

total_records source_count reference_results_count unique_match_ids null_match_ids null_dates null_home_teams null_away_teams null_winners unknown_shooters invalid_winners basic_validation count_validation winner_validation shooter_validation match_id_validation 644 645 48207 644 0 0 0 0 0 414 1 ✅ Validações básicas passaram ✅ Contagem de registros OK ⚠️ 1 vencedores inválidos encontrados ℹ️ 414 primeiros cobradores marcados como "Unknown" ✅ Todos os match_ids são únicos

In [0]:
%sql
-- Identificando a linha com erro
SELECT 
  s.match_id AS match_id,
  s.home_team AS time_mandante,
  s.away_team AS time_visitante,
  s.winner AS vencedor_invalido,
  'O vencedor não é nenhum dos times participantes' AS motivo_invalido
FROM silver.shootouts s
WHERE s.winner NOT IN (s.home_team, s.away_team);

match_id time_mandante time_visitante vencedor_invalido motivo_invalido 2023-07-13_Åland Islands_Falkland Islands_1_1 Åland Islands Falkland Islands Åland O vencedor não é nenhum dos times participantes

In [0]:
%sql
-- Corrigindo o vencedor
SELECT 
  match_id,
  home_team,
  away_team,
  winner AS valor_atual,
  'Åland Islands' AS novo_valor
FROM silver.shootouts
WHERE winner NOT IN (home_team, away_team)
AND (match_id = '2023-07-13_Åland Islands_Falkland Islands_1_1');

-- Execute a atualização (após confirmar os registros acima)
UPDATE silver.shootouts
SET winner = 'Åland Islands'
WHERE winner NOT IN (home_team, away_team)
AND (match_id = '2023-07-13_Åland Islands_Falkland Islands_1_1');

num_affected_rows 1

In [0]:
%sql
-- Verificando se a correção resolveu todos os casos
SELECT 
  COUNT(*) AS registros_problematicos_restantes
FROM silver.shootouts
WHERE winner NOT IN (home_team, away_team);

registros_problematicos_restantes 0

O mesmo procedimento de inserção de comentários é utilizado.

In [0]:
%sql
-- Comentário da tabela
ALTER TABLE silver.shootouts 
SET TBLPROPERTIES (
  'comment' = 'Registro limpo e padronizado de disputas de pênaltis em partidas de futebol. Fonte: bronze.shootouts.'
);

-- Comentários das colunas
ALTER TABLE silver.shootouts CHANGE COLUMN match_date match_date DATE COMMENT 'Data da partida associada à disputa de pênaltis. Domínio: Deve existir em silver.results.match_date.';
ALTER TABLE silver.shootouts CHANGE COLUMN home_team home_team STRING COMMENT 'Time da casa padronizado. Domínio: Valores de silver.results.home_team.';
ALTER TABLE silver.shootouts CHANGE COLUMN away_team away_team STRING COMMENT 'Time visitante padronizado. Domínio: Valores de silver.results.away_team.';
ALTER TABLE silver.shootouts CHANGE COLUMN winner winner STRING COMMENT 'Time vencedor da disputa de pênaltis. Domínio: Valores de home_team ou away_team.';
ALTER TABLE silver.shootouts CHANGE COLUMN first_shooter first_shooter STRING COMMENT 'Time que bateu primeiro nos pênaltis. Domínio: Valores de home_team ou away_team.';

In [0]:
%sql
DESCRIBE TABLE silver.shootouts;

col_name data_type comment match_id string Código único de identificação da partida. Domínio: Até 100 caracteres. match_date date Data da partida associada à disputa de pênaltis. Domínio: Deve existir em silver.results.match_date. home_team string Time da casa padronizado. Domínio: Valores de silver.results.home_team. away_team string Time visitante padronizado. Domínio: Valores de silver.results.away_team. winner string Time vencedor da disputa de pênaltis. Domínio: Valores de home_team ou away_team. first_shooter string Time que bateu primeiro nos pênaltis. Domínio: Valores de home_team ou away_team.

### Tabela Goalscorers
O fluxo de transformação para criação da tabela silver.goalscorers é descrito a seguir:

- Padronização de Datas: Converte date para DATE.

- Unificação de Nomes de Times e Jogadores: Padroniza scoring_team, home_team e away_team via silver.former_names; Não formata scorer (isso será feito na camada Gold).

- Conversão de Flags Booleanas: Transforma own_goal e penalty em BOOLEAN (TRUE/FALSE).

- Filtro de Qualidade: Remove gols sem jogador associado (WHERE scorer IS NOT NULL).

In [0]:
%sql
CREATE OR REPLACE TABLE silver.goalscorers AS
SELECT 
  r.match_id,
  date(g.date) AS match_date,
  COALESCE(fn_team.current, g.team) AS scoring_team,
  COALESCE(fn_home.current, g.home_team) AS home_team,
  COALESCE(fn_away.current, g.away_team) AS away_team,
  COALESCE(g.scorer, 'Unknown') AS scorer,
  -- Minuto como INT ou NULL se não puder converter
  CASE 
    WHEN TRY_CAST(g.minute AS INT) IS NOT NULL THEN CAST(g.minute AS INT)
    ELSE NULL
  END AS minute,
  -- Conversão segura para boolean (trata NULL como false)
  CASE
    WHEN g.own_goal IS NULL THEN false
    WHEN LOWER(g.own_goal) IN ('true', '1', 't', 'y', 'yes') THEN true
    ELSE false
  END AS is_own_goal,
  -- Conversão segura para boolean (trata NULL como false)
  CASE
    WHEN g.penalty IS NULL THEN false
    WHEN LOWER(g.penalty) IN ('true', '1', 't', 'y', 'yes') THEN true
    ELSE false
  END AS is_penalty
FROM bronze.goalscorers g
LEFT JOIN silver.former_names fn_team ON g.team = fn_team.former
LEFT JOIN silver.former_names fn_home ON g.home_team = fn_home.former
LEFT JOIN silver.former_names fn_away ON g.away_team = fn_away.former
JOIN silver.results r
  ON r.match_date = date(g.date)
  AND r.home_team = COALESCE(fn_home.current, g.home_team)
  AND r.away_team = COALESCE(fn_away.current, g.away_team)
WHERE g.scorer IS NOT NULL;

num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE silver.goalscorers AS
SELECT 
  r.match_id,  -- Usando o match_id da tabela results já existente
  date(g.date) AS match_date,
  COALESCE(fn_team.current, g.team) AS scoring_team,
  COALESCE(fn_home.current, g.home_team) AS home_team,
  COALESCE(fn_away.current, g.away_team) AS away_team,
  COALESCE(g.scorer, 'Unknown') AS scorer,
  COALESCE(g.minute, 'Unknown') AS minute,
  CAST(g.own_goal AS BOOLEAN) AS is_own_goal,
  CAST(g.penalty AS BOOLEAN) AS is_penalty
FROM bronze.goalscorers g
JOIN silver.results r
  ON r.home_team = g.home_team
  AND r.away_team = g.away_team
  AND r.match_date = date(g.date)
LEFT JOIN silver.former_names fn_team ON g.team = fn_team.former
LEFT JOIN silver.former_names fn_home ON g.home_team = fn_home.former
LEFT JOIN silver.former_names fn_away ON g.away_team = fn_away.former


num_affected_rows num_inserted_rows

As transformações são validadas.

In [0]:
%sql
-- VERIFICAÇÃO DE QUALIDADE COMPLETA
WITH metrics AS (
  SELECT
    -- Contagens básicas
    COUNT(*) AS total_records,
    (SELECT COUNT(*) FROM bronze.goalscorers WHERE scorer IS NOT NULL) AS bronze_count,
    
    -- Verificação de completude
    SUM(CASE WHEN match_id IS NULL THEN 1 ELSE 0 END) AS null_match_ids,
    SUM(CASE WHEN match_date IS NULL THEN 1 ELSE 0 END) AS null_dates,
    SUM(CASE WHEN scorer = 'Unknown' THEN 1 ELSE 0 END) AS unknown_scorers,
    SUM(CASE WHEN minute IS NULL THEN 1 ELSE 0 END) AS null_minutes,
    
    -- Verificação de consistência
    SUM(CASE WHEN scoring_team NOT IN (home_team, away_team) THEN 1 ELSE 0 END) AS invalid_scoring_teams,
    SUM(CASE WHEN is_own_goal AND scoring_team = home_team THEN 1 ELSE 0 END) AS home_own_goals,
    SUM(CASE WHEN is_own_goal AND scoring_team = away_team THEN 1 ELSE 0 END) AS away_own_goals,
    
    -- Verificação de valores
    SUM(CASE WHEN minute < 0 OR minute > 120 THEN 1 ELSE 0 END) AS invalid_minutes,
    SUM(CASE WHEN NOT is_own_goal AND scoring_team NOT IN (home_team, away_team) THEN 1 ELSE 0 END) AS invalid_regular_goals
),

bronze_metrics AS (
  SELECT
    COUNT(DISTINCT CONCAT(home_team, away_team, date)) AS distinct_matches_bronze
  FROM bronze.goalscorers
  WHERE scorer IS NOT NULL
)

SELECT
  -- Estatísticas básicas
  m.total_records,
  m.bronze_count,
  m.total_records - m.bronze_count AS difference,
  b.distinct_matches_bronze,
  (SELECT COUNT(DISTINCT match_id) FROM silver.results) AS distinct_matches_silver,
  
  -- Relatório de completude
  m.null_match_ids,
  m.null_dates,
  m.unknown_scorers,
  m.null_minutes,
  
  -- Relatório de consistência
  m.invalid_scoring_teams,
  m.home_own_goals,
  m.away_own_goals,
  m.invalid_minutes,
  m.invalid_regular_goals,
  
  -- Resumo de validações (✅/❌)
  CASE
    WHEN m.null_match_ids = 0 AND m.null_dates = 0
    THEN '✅ Chaves primárias válidas'
    ELSE CONCAT('❌ ', m.null_match_ids + m.null_dates, ' chaves nulas')
  END AS key_validation,
  
  CASE
    WHEN m.total_records = m.bronze_count
    THEN '✅ Contagem de registros OK'
    ELSE CONCAT('❌ Diferença de ', ABS(m.total_records - m.bronze_count), ' registros')
  END AS count_validation,
  
  CASE
    WHEN m.invalid_scoring_teams = 0
    THEN '✅ Times marcadores consistentes'
    ELSE CONCAT('⚠️ ', m.invalid_scoring_teams, ' inconsistências')
  END AS team_validation,
  
  CASE
    WHEN m.invalid_minutes = 0
    THEN '✅ Minutos válidos (0-120)'
    ELSE CONCAT('⚠️ ', m.invalid_minutes, ' minutos inválidos')
  END AS minute_validation,
  
  CASE
    WHEN m.unknown_scorers = 0 AND m.null_minutes = 0
    THEN '✅ Dados completos'
    ELSE CONCAT('ℹ️ ', m.unknown_scorers, ' scorers desconhecidos, ', m.null_minutes, ' minutos nulos')
  END AS completeness_validation
FROM metrics m, bronze_metrics b;

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-1347502619220958>:7
      5     display(df)
      6     return df
----> 7   _sqldf = ____databricks_percent_sql()
      8 finally:
      9   del ____databricks_percent_sql

File <command-1347502619220958>:4, in ____databricks_percent_sql()
      2 def ____databricks_percent_sql():
      3   import base64
----> 4   df = spark.sql(base64.standard_b64decode("LS0gVkVSSUZJQ0HDh8ODTyBERSBRVUFMSURBREUgQ09NUExFVEEKV0lUSCBtZXRyaWNzIEFTICgKICBTRUxFQ1QKICAgIC0tIENvbnRhZ2VucyBiw6FzaWNhcwogICAgQ09VTlQoKikgQVMgdG90YWxfcmVjb3JkcywKICAgIChTRUxFQ1QgQ09VTlQoKikgRlJPTSBicm9uemUuZ29hbHNjb3JlcnMgV0hFUkUgc2NvcmVyIElTIE5PVCBOVUxMKSBBUyBicm9uemVfY291bnQsCiAgICAKICAgIC0tIFZlcmlmaWNhw6fDo28gZGUgY29tcGxldHVkZQogICAgU1VNKENBU0UgV0hFTiBtYXRjaF9pZCBJUyBOVUxMIFRIRU4gMSBFTFNFIDAgRU5EKSBBUyBudWxsX21hdGNoX2lkcywKICAgIFNVTShDQVNFIFdIRU4gbWF0Y2hfZGF0ZSBJUyBO

In [0]:
%sql
-- VERIFICAÇÃO DE QUALIDADE COMPLETA (VERSÃO CORRIGIDA)
WITH metrics AS (
  SELECT
    -- Contagens básicas
    COUNT(*) AS total_records,
    (SELECT COUNT(*) FROM bronze.goalscorers WHERE scorer IS NOT NULL) AS bronze_count,
    
    -- Verificação de completude
    SUM(CASE WHEN g.match_id IS NULL THEN 1 ELSE 0 END) AS null_match_ids,
    SUM(CASE WHEN g.match_date IS NULL THEN 1 ELSE 0 END) AS null_dates,
    SUM(CASE WHEN g.scorer = 'Unknown' THEN 1 ELSE 0 END) AS unknown_scorers,
    SUM(CASE WHEN g.minute IS NULL THEN 1 ELSE 0 END) AS null_minutes,
    
    -- Verificação de consistência
    SUM(CASE WHEN g.scoring_team NOT IN (g.home_team, g.away_team) THEN 1 ELSE 0 END) AS invalid_scoring_teams,
    SUM(CASE WHEN g.is_own_goal AND g.scoring_team = g.home_team THEN 1 ELSE 0 END) AS home_own_goals,
    SUM(CASE WHEN g.is_own_goal AND g.scoring_team = g.away_team THEN 1 ELSE 0 END) AS away_own_goals,
    
    -- Verificação de valores
    SUM(CASE WHEN g.minute < 0 OR g.minute > 120 THEN 1 ELSE 0 END) AS invalid_minutes,
    SUM(CASE WHEN NOT g.is_own_goal AND g.scoring_team NOT IN (g.home_team, g.away_team) THEN 1 ELSE 0 END) AS invalid_regular_goals
    
  FROM silver.goalscorers g
),

bronze_metrics AS (
  SELECT
    COUNT(DISTINCT CONCAT(home_team, away_team, date)) AS distinct_matches_bronze
  FROM bronze.goalscorers
  WHERE scorer IS NOT NULL
)

SELECT
  -- Estatísticas básicas
  m.total_records,
  m.bronze_count,
  (m.total_records - m.bronze_count) AS difference,
  b.distinct_matches_bronze,
  (SELECT COUNT(DISTINCT match_id) FROM silver.results) AS distinct_matches_silver,
  
  -- Relatório de completude
  m.null_match_ids,
  m.null_dates,
  m.unknown_scorers,
  m.null_minutes,
  
  -- Relatório de consistência
  m.invalid_scoring_teams,
  m.home_own_goals,
  m.away_own_goals,
  m.invalid_minutes,
  m.invalid_regular_goals,
 
  -- Resumo de validações (✅/❌)
  CASE
    WHEN m.null_match_ids = 0 AND m.null_dates = 0
    THEN '✅ Chaves primárias válidas'
    ELSE CONCAT('❌ ', (m.null_match_ids + m.null_dates), ' chaves nulas')
  END AS key_validation,
  
  CASE
    WHEN m.total_records = m.bronze_count
    THEN '✅ Contagem de registros OK'
    ELSE CONCAT('❌ Diferença de ', ABS(m.total_records - m.bronze_count), ' registros')
  END AS count_validation,
  
  CASE
    WHEN m.invalid_scoring_teams = 0
    THEN '✅ Times marcadores consistentes'
    ELSE CONCAT('⚠️ ', m.invalid_scoring_teams, ' inconsistências')
  END AS team_validation,
  
  CASE
    WHEN m.invalid_minutes = 0
    THEN '✅ Minutos válidos (0-120)'
    ELSE CONCAT('⚠️ ', m.invalid_minutes, ' minutos inválidos')
  END AS minute_validation,
  
  CASE
    WHEN m.unknown_scorers = 0 AND m.null_minutes = 0
    THEN '✅ Dados completos'
    ELSE CONCAT('ℹ️ ', m.unknown_scorers, ' scorers desconhecidos, ', m.null_minutes, ' minutos nulos')
  END AS completeness_validation
FROM metrics m, bronze_metrics b;

total_records bronze_count difference distinct_matches_bronze distinct_matches_silver null_match_ids null_dates unknown_scorers null_minutes invalid_scoring_teams home_own_goals away_own_goals invalid_minutes invalid_regular_goals key_validation count_validation team_validation minute_validation completeness_validation 44289 44313 -24 14370 48190 0 0 0 211 0 488 333 1 0 ✅ Chaves primárias válidas ❌ Diferença de 24 registros ✅ Times marcadores consistentes ⚠️ 1 minutos inválidos ℹ️ 0 scorers desconhecidos, 211 minutos nulos

In [0]:
%sql
-- Consulta para análise de registros faltantes (versão corrigida)
WITH team_mappings AS (
  SELECT
    b.date,
    b.home_team AS bronze_home_team,
    COALESCE(fn_home.current, b.home_team) AS mapped_home_team,
    b.away_team AS bronze_away_team,
    COALESCE(fn_away.current, b.away_team) AS mapped_away_team,
    b.scorer
  FROM bronze.goalscorers b
  LEFT JOIN silver.former_names fn_home ON b.home_team = fn_home.former
  LEFT JOIN silver.former_names fn_away ON b.away_team = fn_away.former
  WHERE b.scorer IS NOT NULL
),

missing_records AS (
  SELECT *
  FROM team_mappings tm
  WHERE NOT EXISTS (
    SELECT 1
    FROM silver.goalscorers s
    JOIN silver.results r ON s.match_id = r.match_id
    WHERE s.scorer = tm.scorer
      AND r.match_date = DATE(tm.date)
  )
)

SELECT 
  m.date,
  m.bronze_home_team,
  r.home_team AS silver_home_team,
  m.bronze_away_team,
  r.away_team AS silver_away_team,
  CASE 
    WHEN r.match_id IS NULL THEN '❌ Não encontrado em silver.results'
    ELSE '✅ Encontrado'
  END AS status
FROM missing_records m
LEFT JOIN silver.results r ON 
  r.match_date = DATE(m.date)
  AND r.home_team = m.mapped_home_team
  AND r.away_team = m.mapped_away_team
LIMIT 24;

date bronze_home_team silver_home_team bronze_away_team silver_away_team status 1993-04-28 Czech Republic null Wales null ❌ Não encontrado em silver.results 1993-09-08 Wales null Czech Republic null ❌ Não encontrado em silver.results 1993-10-27 Czech Republic null Cyprus null ❌ Não encontrado em silver.results 1993-09-08 Wales null Czech Republic null ❌ Não encontrado em silver.results 1993-06-16 Faroe Islands null Czech Republic null ❌ Não encontrado em silver.results 1993-06-16 Faroe Islands null Czech Republic null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-10-27 Czech Republic null Cyprus null ❌ Não encontrado em silver.results 1993-06-16 Faroe Islands null Czech Republic null ❌ Não encontrado em silver.results 1993-10-27 Czech Republic null Cyprus null ❌ Não encontrado em silver.results 1993-04-28 Czech Republic null Wales null ❌ Não encontrado em silver.results 1993-03-24 Cyprus null Czech Republic null ❌ Não encontrado em silver.results 1993-03-24 Cyprus null Czech Republic null ❌ Não encontrado em silver.results 1993-09-08 Wales null Czech Republic null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-06-02 Czech Republic null Romania null ❌ Não encontrado em silver.results 1993-09-08 Wales null Czech Republic null ❌ Não encontrado em silver.results 1922-10-22 Brazil null Paraguay null ❌ Não encontrado em silver.results 1922-10-22 Brazil null Paraguay null ❌ Não encontrado em silver.results 1922-10-22 Brazil null Paraguay null ❌ Não encontrado em silver.results

In [0]:
%sql
DESCRIBE TABLE silver.goalscorers

col_name data_type comment match_id string Código único de identificação da partida. Domínio: Até 100 caracteres. match_date date null scoring_team string null home_team string null away_team string null scorer string null minute int null is_own_goal boolean null is_penalty boolean null

### Tabela FIFA_Ranking
O fluxo de transformação para criação da tabela silver.fifa_ranking é descrito a seguir:
- Padronização de Datas: Converte rank_date para DATE.

- Unificação de Nomes de Países: Usa silver.former_names para garantir consistência.

- Conversão de Tipos Numéricos: Converte rank para INT e total_points para DECIMAL(10,2).

In [0]:
%sql
CREATE OR REPLACE TABLE silver.fifa_ranking AS
SELECT 
  date(r.rank_date) AS rank_date,
  COALESCE(fn.current, r.country_full) AS country,
  CAST(r.rank AS INT) AS rank,
  CAST(r.total_points AS DECIMAL(10,2)) AS total_points
FROM bronze.fifa_ranking r
LEFT JOIN silver.former_names fn ON r.country_full = fn.former;

num_affected_rows num_inserted_rows

In [0]:
%sql
-- Verificação de qualidade dos dados após transformação
WITH checks AS (
  SELECT
    -- Verificação básica de completude
    COUNT(*) AS total_records,
    SUM(CASE WHEN f.rank_date IS NULL THEN 1 ELSE 0 END) AS null_dates,
    SUM(CASE WHEN f.country IS NULL THEN 1 ELSE 0 END) AS null_countries,
    SUM(CASE WHEN f.rank IS NULL THEN 1 ELSE 0 END) AS null_ranks,
    SUM(CASE WHEN f.total_points IS NULL THEN 1 ELSE 0 END) AS null_points,
    
    -- Verificação de valores
    SUM(CASE WHEN f.rank < 1 OR f.rank > 300 THEN 1 ELSE 0 END) AS invalid_ranks,
    SUM(CASE WHEN f.total_points < 0 OR f.total_points > 3000 THEN 1 ELSE 0 END) AS invalid_points,
    
    -- Verificação de mapeamento de países
    SUM(CASE WHEN fn.former IS NULL AND r.country_full != f.country THEN 1 ELSE 0 END) AS unmapped_countries,
    
    -- Verificação de integridade referencial
    (SELECT COUNT(*) FROM bronze.fifa_ranking) AS source_count,
    (SELECT COUNT(DISTINCT country_full) FROM bronze.fifa_ranking) AS source_unique_countries
  FROM silver.fifa_ranking f
  LEFT JOIN bronze.fifa_ranking r ON date(r.rank_date) = f.rank_date AND r.country_full = f.country
  LEFT JOIN silver.former_names fn ON r.country_full = fn.former
)

SELECT
  total_records,
  source_count,
  source_unique_countries,
  
  -- Relatório de completude
  null_dates,
  null_countries,
  null_ranks,
  null_points,
  
  -- Relatório de qualidade
  invalid_ranks,
  invalid_points,
  unmapped_countries,
  
  -- Resumo de validações
  CASE
    WHEN null_dates = 0 AND null_countries = 0 AND null_ranks = 0 AND null_points = 0
    THEN '✅ Validações básicas passaram'
    ELSE '❌ Problemas encontrados nos dados'
  END AS basic_validation,
  
  CASE
    WHEN total_records BETWEEN source_count * 0.95 AND source_count * 1.05
    THEN '✅ Contagem de registros dentro do esperado'
    ELSE CONCAT('⚠️ Diferença de ', ABS(total_records - source_count), ' registros')
  END AS count_validation,
  
  CASE
    WHEN invalid_ranks = 0 AND invalid_points = 0
    THEN '✅ Todos os valores numéricos são válidos'
    ELSE CONCAT('⚠️ ', invalid_ranks + invalid_points, ' valores inválidos encontrados')
  END AS numeric_validation,
  
  CASE
    WHEN unmapped_countries = 0
    THEN '✅ Todos os países foram mapeados corretamente'
    ELSE CONCAT('ℹ️ ', unmapped_countries, ' países sem mapeamento completo')
  END AS country_mapping_validation
FROM checks;

total_records source_count source_unique_countries null_dates null_countries null_ranks null_points invalid_ranks invalid_points unmapped_countries basic_validation count_validation numeric_validation country_mapping_validation 67472 67472 216 0 0 9 0 0 0 0 ❌ Problemas encontrados nos dados ✅ Contagem de registros dentro do esperado ✅ Todos os valores numéricos são válidos ✅ Todos os países foram mapeados corretamente

Foram encontrados 9 valores null na coluna referente ao ranking. Os mesmos são listados e em seguida é realizada a correção, deletando os mesmos da lista, pois não é um dado possível de ser substituído por algum valor arbitrário.

In [0]:
%sql
SELECT *
FROM silver.fifa_ranking
WHERE rank IS NULL OR rank < 1 OR rank > 216; -- Assumindo que há 211 países no ranking

rank_date country rank total_points 2023-10-26 Eritrea null 855.56 2023-10-26 Tonga null 861.81 2023-10-26 Samoa null 894.26 2023-10-26 American Samoa null 900.27 2023-11-30 Eritrea null 855.56 2023-12-21 Eritrea null 855.56 2024-02-15 Eritrea null 855.56 2024-04-04 Eritrea null 855.56 2024-06-20 Eritrea null 855.56

In [0]:
%sql
DELETE FROM silver.fifa_ranking
WHERE rank IS NULL OR rank < 1 OR rank > 216;

num_affected_rows 9

Verificando a exclusão.

In [0]:
%sql
SELECT *
FROM silver.fifa_ranking
WHERE rank IS NULL OR rank < 1 OR rank > 216; -- Assumindo que há 216 países no ranking

rank_date country rank total_points

Também são atualizados os nomes de alguns países para ficar de acordo com o registrado na tabela results.

In [0]:
%sql
-- Atualiza os nomes dos países na tabela silver.ranking para padronização
UPDATE silver.fifa_ranking
SET country = CASE 
    WHEN country = 'Brunei Darussalam' THEN 'Brunei'
    WHEN country = 'Congo DR' THEN 'DR Congo'
    WHEN country = 'Chinese Taipei' THEN 'Taiwan'
    WHEN country = 'Cabo Verde' THEN 'Cape Verde'
    WHEN country = 'Curacao' THEN 'Curaçao'
    WHEN country = 'Czechia' THEN 'Czech Republic'
    WHEN country = 'The Gambia' THEN 'Gambia'
    WHEN country = 'IR Iran' THEN 'Iran'
    WHEN country = "Côte d'Ivoire" THEN 'Ivory Coast'
    WHEN country = 'Kyrgyz Republic' THEN 'Kyrgyzstan'
    WHEN country = 'Korea DPR' THEN 'North Korea'
    WHEN country = 'St Kitts and Nevis' THEN 'Saint Kitts and Nevis'
    WHEN country = 'St Lucia' THEN 'Saint Lucia'
    WHEN country = 'Korea Republic' THEN 'South Korea'
    WHEN country = 'Sao Tome and Principe' THEN 'São Tomé and Príncipe'
    WHEN country = 'USA' THEN 'United States'
    WHEN country = 'St Vincent and the Grenadines' THEN 'Saint Vincent and the Grenadines'
    WHEN country = 'US Virgin Islands' THEN 'United States Virgin Islands'
    ELSE country
END
WHERE country IN (
    'Brunei Darussalam', 'Congo DR', 'Chinese Taipei', 'Cabo Verde', 
    'Curacao', 'Czechia', 'The Gambia', 'IR Iran', "Côte d'Ivoire", 
    'Korea DPR', 'St Kitts and Nevis', 'St Lucia', 'Korea Republic', 
    'Sao Tome and Principe', 'USA', 'Kyrgyz Republic', 
    'St Vincent and the Grenadines', 'US Virgin Islands'
);

num_affected_rows 5594

In [0]:
%sql
SELECT DISTINCT country FROM silver.fifa_ranking
WHERE country IN ('Brunei', 'DR Congo', 'Taiwan', 'Cape Verde', 'Curaçao', 
                      'Czech Republic', 'Gambia', 'Iran', 'Ivory Coast', 
                      'North Korea', 'Saint Kitts and Nevis', 'Saint Lucia', 
                      'South Korea', 'São Tomé and Príncipe','Kyrgyzstan',
                      'Saint Vincent and the Grenadines', 
                      'United States Virgin Islands')
ORDER BY country;

country Brunei Cape Verde Curaçao Czech Republic DR Congo Gambia Iran Ivory Coast Kyrgyzstan North Korea Saint Kitts and Nevis Saint Lucia Saint Vincent and the Grenadines South Korea São Tomé and Príncipe Taiwan United States Virgin Islands

In [0]:
%sql
DESCRIBE TABLE silver.fifa_ranking

col_name data_type comment rank_date date null country string null rank int null total_points decimal(10,2) null

Com a camada silver concluída, seguimos agora para a camada gold, onde as tabelas serão modeladas com agregações e métricas que permitirão responder às perguntas de negócio e extrair insights sobre a dominância histórica das seleções nacionais no futebol.

## Camada Gold

A camada Gold representa o estágio final do pipeline de dados, onde os dados limpos e padronizados da camada Silver são transformados em modelos analíticos prontos para consumo. 

O modelo de dados desenvolvido para a camada gold segue a abordagem estrela (star schema), uma estrutura amplamente utilizada em Data Warehousing para otimizar análises e consultas.

## 2. Estrutura do Modelo Estrela
O modelo é composto por **uma tabela fato** e **três tabelas dimensão**, permitindo análises históricas detalhadas sobre o desempenho das seleções.

### 2.1. Tabela Fato: `gold.match_performance`
A tabela **`gold.match_performance`** contém informações detalhadas sobre cada partida registrada na base de dados.  
Ela serve como o **centro da análise**, permitindo correlações com diversas métricas de desempenho.

**📌 Principais atributos:**  
- **Identificação do jogo** (`match_id`, `match_date`)  
- **Seleções envolvidas** (`home_team`, `away_team`)  
- **Resultados** (`home_score`, `away_score`)  
- **Ranking FIFA antes do jogo** (`home_team_rank`, `away_team_rank`)  
- **Características da partida** (`tournament`, `is_neutral`)

Essa estrutura permite analisar **o desempenho histórico das seleções em competições e amistosos**.

---

### 2.2. Tabela Dimensão: `gold.team_stats`
A **`gold.team_stats`** armazena estatísticas agregadas de cada seleção ao longo do tempo, consolidando métricas essenciais para medir seu desempenho.

**📌 Principais atributos:**  
- **Identificação da seleção** (`team_id`, `team_name`)  
- **Total de partidas jogadas** (`total_matches`)  
- **Total de vitórias, empates e derrotas** (`wins`, `draws`, `losses`)  
- **Gols marcados e sofridos** (`goals_for`, `goals_against`)  
- **Saldo de gols** (`goal_difference`)  
- **Número de partidas sem sofrer gols** (`clean_sheets`)  
- **Total de pontos acumulados** (`points`)  
- **Taxa de aproveitamento (%)** (`win_percentage`)

Essa dimensão permite análises sobre **consistência e desempenho geral das seleções**.

---

### 2.3. Tabela Dimensão: `gold.penalty_shootouts`
A **`gold.penalty_shootouts`** registra informações detalhadas sobre disputas de pênaltis, incluindo **o vencedor da disputa e o primeiro batedor**.

**📌 Principais atributos:**  
- **Identificação da partida** (`match_id`, `match_date`)  
- **Seleções envolvidas** (`home_team`, `away_team`)  
- **Vencedor da disputa** (`penalty_winner`)  
- **Perdedor da disputa** (`penalty_loser`)  
- **Primeiro jogador a bater pênalti** (`first_penalty_shooter`)

Essa tabela auxilia na análise de **desempenho das seleções em decisões por pênaltis**, algo relevante para identificar times dominantes.

---

### 2.4. Tabela Dimensão: `gold.top_scores`
A **`gold.top_scores`** armazena informações sobre **os principais artilheiros** da história, relacionando seu desempenho com os resultados das seleções.

**📌 Principais atributos:**  
- **Identificação da partida** (`match_id`, `match_date`)  
- **Nome do jogador** (`player_name`)  
- **Seleção do jogador** (`team`)  
- **Número de gols marcados** (`goals_scored`)  
- **Total de partidas jogadas** (`total_matches`)  
- **Média de gols por partida** (`avg_goals_per_match`)

Essa dimensão permite entender **o impacto dos artilheiros no sucesso das seleções**.

---

## 3. Relacionamentos do Modelo
A estrutura do **modelo estrela** garante que todas as tabelas **se conectam através da tabela fato (`gold.match_performance`)**, permitindo análises eficientes e rápidas.

📌 **Relacionamentos principais:**  
- `gold.match_performance` 🔄 `gold.team_stats` → Relacionamento por `home_team` e `away_team`  
- `gold.match_performance` 🔄 `gold.penalty_shootouts` → Relacionamento por `match_id`  
- `gold.match_performance` 🔄 `gold.top_scores` → Relacionamento por `match_id`  

Essa abordagem permite **agregações rápidas**, mantendo **alta performance e flexibilidade** para responder às perguntas analíticas.

---

## 4. Justificativa da Escolha do Modelo Estrela
Optamos pelo **modelo estrela** pois ele:  
✅ **Facilita consultas analíticas complexas**, otimizando cálculos e agrupamentos.  
✅ **Garante eficiência computacional**, evitando duplicação desnecessária de dados.  
✅ **Proporciona flexibilidade**, permitindo a inclusão de novas dimensões no futuro.  
✅ **Reduz a complexidade da modelagem**, tornando o esquema mais intuitivo e direto.  




In [0]:
%sql DROP DATABASE IF EXISTS gold CASCADE

In [0]:
%sql CREATE DATABASE gold

In [0]:
%sql
CREATE TABLE gold.team_stats AS
SELECT
    team AS team_id,
    team AS team_name,
    COUNT(*) AS total_matches,
    SUM(CASE WHEN goals_for > goals_against THEN 1 ELSE 0 END) AS wins,
    SUM(CASE WHEN goals_for = goals_against THEN 1 ELSE 0 END) AS draws,
    SUM(CASE WHEN goals_for < goals_against THEN 1 ELSE 0 END) AS losses,
    SUM(goals_for) AS goals_for,
    SUM(goals_against) AS goals_against,
    SUM(goals_for) - SUM(goals_against) AS goal_difference,
    SUM(CASE WHEN goals_against = 0 THEN 1 ELSE 0 END) AS clean_sheets,
    (SUM(CASE WHEN goals_for > goals_against THEN 3 ELSE 0 END) + 
     SUM(CASE WHEN goals_for = goals_against THEN 1 ELSE 0 END)) AS points,
    ROUND(
        SUM(CASE WHEN goals_for > goals_against THEN 1 ELSE 0 END) * 100.0 / COUNT(*),
        2
    ) AS win_percentage
FROM (
    SELECT home_team AS team, home_score AS goals_for, away_score AS goals_against FROM silver.results
    UNION ALL
    SELECT away_team AS team, away_score AS goals_for, home_score AS goals_against FROM silver.results
) AS matches
GROUP BY team;


num_affected_rows num_inserted_rows

In [0]:
%sql
SELECT* 
FROM gold.team_stats
ORDER BY goals_for DESC

team_id team_name total_matches wins draws losses goals_for goals_against goal_difference clean_sheets points win_percentage England England 1078 616 257 205 2355 1036 1319 446 2105 57.14 Germany Germany 1019 590 213 216 2291 1186 1105 350 1983 57.90 Brazil Brazil 1047 665 214 168 2279 946 1333 467 2209 63.51 Sweden Sweden 1089 537 230 322 2152 1398 754 357 1841 49.31 Argentina Argentina 1055 581 256 218 1995 1070 925 410 1999 55.07 Hungary Hungary 994 466 219 309 1992 1468 524 278 1617 46.88 Netherlands Netherlands 867 445 195 227 1809 1068 741 307 1530 51.33 South Korea South Korea 995 530 251 214 1771 902 869 459 1841 53.27 Mexico Mexico 982 503 224 255 1736 1036 700 402 1733 51.22 France France 923 468 194 261 1684 1195 489 331 1598 50.70 Spain Spain 771 453 178 140 1567 693 874 331 1537 58.75 Denmark Denmark 862 395 181 286 1556 1162 394 254 1366 45.82 Italy Italy 881 468 242 171 1539 863 676 354 1646 53.12 Uruguay Uruguay 956 421 235 300 1514 1166 348 323 1498 44.04 Austria Austria 849 358 183 308 1512 1310 202 210 1257 42.17 Belgium Belgium 841 374 177 290 1508 1280 228 252 1299 44.47 Poland Poland 880 378 222 280 1479 1186 293 277 1356 42.95 Japan Japan 784 384 163 237 1432 925 507 296 1315 48.98 Scotland Scotland 839 395 181 263 1428 1037 391 268 1366 47.08 Thailand Thailand 853 331 204 318 1362 1270 92 263 1197 38.80 Malaysia Malaysia 827 321 191 315 1346 1205 141 244 1154 38.81 Norway Norway 860 320 193 347 1316 1408 -92 235 1153 37.21 China PR China PR 704 345 152 207 1312 769 543 277 1187 49.01 Switzerland Switzerland 871 309 199 363 1289 1434 -145 211 1126 35.48 Russia Russia 736 378 193 165 1277 725 552 302 1327 51.36 Trinidad and Tobago Trinidad and Tobago 734 319 157 258 1246 963 283 225 1114 43.46 Zambia Zambia 782 355 201 226 1226 833 393 301 1266 45.40 Romania Romania 753 329 193 231 1218 960 258 238 1180 43.69 Costa Rica Costa Rica 708 311 171 226 1209 832 377 234 1104 43.93 Indonesia Indonesia 718 277 141 300 1201 1168 33 200 972 38.58 Egypt Egypt 734 370 176 188 1199 749 450 307 1286 50.41 Portugal Portugal 683 341 156 186 1197 766 431 275 1179 49.93 United States United States 772 342 159 271 1168 1019 149 282 1185 44.30 Chile Chile 823 310 178 335 1161 1170 -9 229 1108 37.67 Australia Australia 569 289 122 158 1151 608 543 226 989 50.79 Iran Iran 602 344 142 116 1138 477 661 297 1174 57.14 Saudi Arabia Saudi Arabia 718 341 166 211 1112 752 360 299 1189 47.49 Kuwait Kuwait 673 283 175 215 1052 746 306 238 1024 42.05 Ghana Ghana 657 307 172 178 1034 681 353 246 1093 46.73 Uganda Uganda 672 280 180 212 1015 789 226 239 1020 41.67 Ivory Coast Ivory Coast 620 315 159 146 1013 629 384 249 1104 50.81 Bulgaria Bulgaria 723 259 185 279 997 1074 -77 195 962 35.82 Paraguay Paraguay 772 270 206 296 989 1103 -114 233 1016 34.97 Iraq Iraq 639 295 185 159 989 596 393 261 1070 46.17 Czechoslovakia Czechoslovakia 520 236 119 165 984 721 263 135 827 45.38 Kenya Kenya 694 264 171 259 963 940 23 196 963 38.04 Nigeria Nigeria 636 298 183 155 962 638 324 263 1077 46.86 Finland Finland 806 212 165 429 947 1655 -708 165 801 26.30 Yugoslavia Yugoslavia 485 223 98 164 943 760 183 124 767 45.98 Tunisia Tunisia 656 286 183 187 938 666 272 256 1041 43.60 Singapore Singapore 686 214 139 333 919 1256 -337 161 781 31.20 Algeria Algeria 593 271 157 165 900 600 300 230 970 45.70 Honduras Honduras 605 241 156 208 894 783 111 194 879 39.83 Wales Wales 714 230 162 322 889 1142 -253 197 852 32.21 Qatar Qatar 622 258 150 214 885 747 138 211 924 41.48 Turkey Turkey 630 250 151 229 872 889 -17 201 901 39.68 Cameroon Cameroon 602 266 187 149 864 638 226 231 985 44.19 Jamaica Jamaica 644 248 151 245 855 856 -1 218 895 38.51 Peru Peru 703 230 172 301 851 981 -130 194 862 32.72 Morocco Morocco 589 283 167 139 851 486 365 281 1016 48.05 United Arab Emirates United Arab Emirates 599 242 147 210 851 744 107 206 873 40.40 Republic of Ireland Republic of Ireland 620 238 173 209 839 758 81 222 887 38.39 Senegal Senegal 617 283 166 168 834 584 250 252 1

In [0]:
%sql
-- Criar a tabela antes de inserir os dados
CREATE TABLE IF NOT EXISTS gold.match_performance (
    match_id STRING,
    match_date DATE,
    home_team STRING,
    away_team STRING,
    home_score INT,
    away_score INT,
    home_team_rank INT,
    away_team_rank INT,
    tournament STRING,
    is_neutral BOOLEAN
);

-- Inserir os dados na tabela
INSERT OVERWRITE gold.match_performance
WITH latest_ranking AS (
    SELECT country, rank_date, rank,
           ROW_NUMBER() OVER (PARTITION BY country ORDER BY rank_date DESC) AS rn
    FROM silver.fifa_ranking
)

SELECT 
    r.match_id,
    r.match_date,
    r.home_team,
    r.away_team,
    r.home_score,
    r.away_score,
    hr.rank AS home_team_rank,
    ar.rank AS away_team_rank,
    r.tournament,
    r.is_neutral
FROM silver.results r
LEFT JOIN latest_ranking hr
    ON hr.country = r.home_team
    AND hr.rank_date <= r.match_date
    AND hr.rn = 1  -- Apenas o ranking mais recente antes da partida
LEFT JOIN latest_ranking ar
    ON ar.country = r.away_team
    AND ar.rank_date <= r.match_date
    AND ar.rn = 1;  -- Apenas o ranking mais recente antes da partida


num_affected_rows num_inserted_rows 48207 48207

In [0]:
%sql
SELECT *
FROM gold.match_performance
ORDER BY match_date DESC

match_id match_date home_team away_team home_score away_score home_team_rank away_team_rank tournament is_neutral 2025-03-25_Tajikistan_Timor-Leste_1_0 2025-03-25 Tajikistan Timor-Leste 1 0 102 196 AFC Asian Cup qualification false 2025-03-25_Philippines_Maldives_4_1 2025-03-25 Philippines Maldives 4 1 147 160 AFC Asian Cup qualification false 2025-03-25_Bhutan_Yemen_0_0 2025-03-25 Bhutan Yemen 0 0 183 155 AFC Asian Cup qualification false 2025-03-25_Lebanon_Brunei_5_0 2025-03-25 Lebanon Brunei 5 0 117 191 AFC Asian Cup qualification true 2025-03-25_India_Bangladesh_0_0 2025-03-25 India Bangladesh 0 0 124 185 AFC Asian Cup qualification false 2025-03-25_Singapore_Hong Kong_0_0 2025-03-25 Singapore Hong Kong 0 0 159 157 AFC Asian Cup qualification false 2025-03-25_Taiwan_Turkmenistan_1_2 2025-03-25 Taiwan Turkmenistan 1 2 163 144 AFC Asian Cup qualification false 2025-03-25_Thailand_Sri Lanka_1_0 2025-03-25 Thailand Sri Lanka 1 0 100 205 AFC Asian Cup qualification false 2025-03-25_Myanmar_Afghanistan_2_1 2025-03-25 Myanmar Afghanistan 2 1 164 151 AFC Asian Cup qualification false 2025-03-25_Syria_Pakistan_2_0 2025-03-25 Syria Pakistan 2 0 93 197 AFC Asian Cup qualification true 2025-03-25_Vietnam_Laos_5_0 2025-03-25 Vietnam Laos 5 0 116 189 AFC Asian Cup qualification false 2025-03-25_Malaysia_Nepal_2_0 2025-03-25 Malaysia Nepal 2 0 135 175 AFC Asian Cup qualification false 2025-03-25_Costa Rica_Belize_6_1 2025-03-25 Costa Rica Belize 6 1 52 184 Gold Cup qualification false 2025-03-25_Guatemala_Guyana_2_0 2025-03-25 Guatemala Guyana 2 0 106 153 Gold Cup qualification false 2025-03-25_Honduras_Bermuda_2_0 2025-03-25 Honduras Bermuda 2 0 78 171 Gold Cup qualification false 2025-03-25_Jamaica_Saint Vincent and the Grenadines_3_0 2025-03-25 Jamaica Saint Vincent and the Grenadines 3 0 53 174 Gold Cup qualification false 2025-03-25_Martinique_Suriname_0_1 2025-03-25 Martinique Suriname 0 1 null 141 Gold Cup qualification false 2025-03-25_Nicaragua_Guadeloupe_0_1 2025-03-25 Nicaragua Guadeloupe 0 1 130 null Gold Cup qualification false 2025-03-25_Trinidad and Tobago_Cuba_4_0 2025-03-25 Trinidad and Tobago Cuba 4 0 99 169 Gold Cup qualification false 2025-03-25_Azerbaijan_Belarus_0_2 2025-03-25 Azerbaijan Belarus 0 2 111 98 Friendly false 2025-03-25_Russia_Zambia_5_0 2025-03-25 Russia Zambia 5 0 33 90 Friendly false 2025-03-25_Cambodia_Aruba_1_2 2025-03-25 Cambodia Aruba 1 2 180 194 Friendly false 2025-03-25_Dominican Republic_Puerto Rico_2_0 2025-03-25 Dominican Republic Puerto Rico 2 0 150 156 Friendly false 2025-03-25_Niger_Bonaire_6_0 2025-03-25 Niger Bonaire 6 0 128 null Friendly true 2025-03-25_Sweden_Northern Ireland_5_1 2025-03-25 Sweden Northern Ireland 5 1 28 73 Friendly false 2025-03-25_Switzerland_Luxembourg_3_1 2025-03-25 Switzerland Luxembourg 3 1 19 85 Friendly false 2025-03-25_Bolivia_Uruguay_0_0 2025-03-25 Bolivia Uruguay 0 0 84 14 FIFA World Cup qualification false 2025-03-25_Colombia_Paraguay_2_2 2025-03-25 Colombia Paraguay 2 2 12 58 FIFA World Cup qualification false 2025-03-25_Venezuela_Peru_1_0 2025-03-25 Venezuela Peru 1 0 54 31 FIFA World Cup qualification false 2025-03-25_Argentina_Brazil_4_1 2025-03-25 Argentina Brazil 4 1 1 4 FIFA World Cup qualification false 2025-03-25_Chile_Ecuador_0_0 2025-03-25 Chile Ecuador 0 0 40 30 FIFA World Cup qualification false 2025-03-25_Iran_Uzbekistan_2_2 2025-03-25 Iran Uzbekistan 2 2 20 62 FIFA World Cup qualification false 2025-03-25_Kyrgyzstan_Qatar_3_1 2025-03-25 Kyrgyzstan Qatar 3 1 101 35 FIFA World Cup qualification false 2025-03-25_North Korea_United Arab Emirates_1_2 2025-03-25 North Korea United Arab Emirates 1 2 110 69 FIFA World Cup qualification true 2025-03-25_South Korea_Jordan_1_1 2025-03-25 South Korea Jordan 1 1 22 68 FIFA World Cup qualification false 2025-03-25_Kuwait_Oman_0_1 2025-03-25 Kuwait Oman 0 1 137 76 FIFA World Cup qualification false 2025-03-25_Palestine_Iraq_2_1 2025-03-25 Palestine Iraq 2 1 95 55 FIFA World Cup qualification true 2025-03-25

In [0]:
%sql
CREATE TABLE gold.top_scorers AS
SELECT
    gsc.scorer AS player_name,
    gsc.scoring_team AS team_name,
    COUNT(*) AS total_goals,
    COUNT(DISTINCT gsc.match_id) AS matches_scored,
    ROUND(COUNT(*) * 1.0 / COUNT(DISTINCT gsc.match_id), 2) AS avg_goals_per_game
FROM silver.goalscorers gsc
GROUP BY gsc.scorer, gsc.scoring_team;


num_affected_rows num_inserted_rows

In [0]:
%sql
SELECT *
FROM gold.top_scorers
ORDER BY total_goals DESC

player_name team_name total_goals matches_scored avg_goals_per_game Cristiano Ronaldo Portugal 108 67 1.61 Robert Lewandowski Poland 63 40 1.58 Romelu Lukaku Belgium 60 37 1.62 Harry Kane England 58 42 1.38 Lionel Messi Argentina 55 44 1.25 Edin Džeko Bosnia and Herzegovina 50 38 1.32 Ali Daei Iran 49 34 1.44 Miroslav Klose Germany 48 34 1.41 Aleksandar Mitrović Serbia 47 32 1.47 Carlos Ruiz Guatemala 47 30 1.57 Luis Suárez Uruguay 47 37 1.27 Robbie Keane Republic of Ireland 44 32 1.38 Zlatan Ibrahimović Sweden 44 32 1.38 Clint Dempsey United States 41 34 1.21 David Villa Spain 41 29 1.41 Andriy Shevchenko Ukraine 40 35 1.14 Samuel Eto'o Cameroon 40 33 1.21 Ronaldo Brazil 39 26 1.50 Hakan Şükür Turkey 39 27 1.44 Gerd Müller Germany 39 24 1.63 Landon Donovan United States 38 31 1.23 Kylian Mbappé France 38 26 1.46 Paulo Wanchope Costa Rica 37 25 1.48 Jared Borgetti Mexico 37 26 1.42 Gabriel Batistuta Argentina 37 27 1.37 Wayne Rooney England 37 30 1.23 Tim Cahill Australia 36 24 1.50 Jon Dahl Tomasson Denmark 36 29 1.24 Robin van Persie Netherlands 35 26 1.35 Gareth Bale Wales 35 28 1.25 Thomas Müller Germany 35 24 1.46 Memphis Depay Netherlands 35 25 1.40 Cuauhtémoc Blanco Mexico 34 24 1.42 Carlos Pavón Honduras 34 23 1.48 Thierry Henry France 34 29 1.17 Jan Koller Czech Republic 33 25 1.32 Romário Brazil 33 23 1.43 Karim Bagheri Iran 32 18 1.78 Ali Mabkhout United Arab Emirates 32 22 1.45 Karl-Heinz Rummenigge Germany 32 21 1.52 Raúl Spain 32 25 1.28 Teemu Pukki Finland 31 26 1.19 Didier Drogba Ivory Coast 31 25 1.24 Neymar Brazil 31 26 1.19 Eran Zahavi Israel 31 22 1.41 Davor Šuker Croatia 31 25 1.24 Jürgen Klinsmann Germany 30 25 1.20 Edinson Cavani Uruguay 30 26 1.15 Alexis Sánchez Chile 30 24 1.25 Kazuyoshi Miura Japan 30 15 2.00 Ruud van Nistelrooy Netherlands 29 22 1.32 Antoine Griezmann France 29 25 1.16 Sardar Azmoun Iran 29 22 1.32 Toni Polster Austria 29 19 1.53 Lukas Podolski Germany 29 22 1.32 Álvaro Morata Spain 29 23 1.26 Hristo Stoichkov Bulgaria 28 24 1.17 Andriy Yarmolenko Ukraine 28 25 1.12 Olivier Giroud France 28 23 1.22 Diego Forlán Uruguay 28 22 1.27 Fernando Torres Spain 28 17 1.65 Dimitar Berbatov Bulgaria 28 20 1.40 Marko Arnautović Austria 28 21 1.33 Gheorghe Hagi Romania 27 24 1.13 Michael Owen England 27 22 1.23 Dennis Bergkamp Netherlands 27 22 1.23 Henrik Larsson Sweden 27 21 1.29 Artem Dzyuba Russia 27 18 1.50 Michel Platini France 27 21 1.29 Michael Ballack Germany 27 26 1.04 Christian Eriksen Denmark 27 20 1.35 Kubilay Türkyilmaz Switzerland 26 18 1.44 Rudi Völler Germany 26 19 1.37 Klaas-Jan Huntelaar Netherlands 26 20 1.30 Preben Elkjær Denmark 26 18 1.44 Hernán Crespo Argentina 26 23 1.13 Savo Milošević Serbia 26 21 1.24 Pelé Brazil 26 17 1.53 Eduardo Vargas Chile 26 19 1.37 Eusébio Portugal 26 18 1.44 Johan Cruyff Netherlands 25 16 1.56 Pauleta Portugal 25 18 1.39 Damian Mori Australia 25 11 2.27 Fernando Hierro Spain 25 25 1.00 Ivan Perišić Croatia 25 24 1.04 Milan Baroš Czech Republic 25 20 1.25 Marcelo Martins Moreno Bolivia 25 21 1.19 Iván Zamorano Chile 25 18 1.39 Son Heung-min South Korea 25 20 1.25 Ferenc Bene Hungary 25 22 1.14 Paolo Guerrero Peru 25 20 1.25 Joachim Streich German DR 25 19 1.32 Xherdan Shaqiri Switzerland 25 19 1.32 Eden Hazard Belgium 25 21 1.19 Alexander Frei Switzerland 24 20 1.20 Zlatko Zahovič Slovenia 24 20 1.20 Javier Hernández Mexico 24 19 1.26 Jozy Altidore United States 24 19 1.26 Māris Verpakovskis Latvia 24 19 1.26 Adrian Mutu Romania 24 19 1.26 Stevan Jovetić Montenegro 24 19 1.26 Asamoah Gyan Ghana 24 22 1.09 Georginio Wijnaldum Netherlands 24 19 1.26 Blas Pérez Panama 24 19 1.26 Gylfi Sigurðsson Iceland 24 19 1.26 Arturo Vidal Chile 24 19 1.26 Patrick M'Boma Cameroon 24 18 1.33 Luis Tejada Panama 24 21 1.14 Islam Slimani Algeria 23 15 1.53 Erling Haaland Norway 23 14 1.64 Ádám Szalai Hungary 23 19 1.21 Mehdi Taremi Iran 23 18 1.28 Gonzalo Higuaín Argentina 23 16 1.44 Stern John Trinidad and Tobago 23 17 1.35 Predrag Mijatović Serbia 23 18 1.28 Ahmed 

In [0]:
%sql
CREATE OR REPLACE TABLE gold.penalty_shootouts AS
SELECT
    s.match_id,
    s.match_date,
    s.home_team,
    s.away_team,
    s.winner AS penalty_winner,
    CASE 
        WHEN s.winner = s.home_team THEN s.away_team
        ELSE s.home_team
    END AS penalty_loser,
    s.first_shooter AS first_penalty_shooter
FROM silver.shootouts s;


num_affected_rows num_inserted_rows

## Solução do problema